$\newcommand\N{\mathbb N}
\newcommand\Z{\mathbb Z}
\newcommand\Q{\mathbb Q}
\newcommand\R{\mathbb R}
\newcommand\C{\mathbb C}
\newcommand\too\longrightarrow
\renewcommand\phi\varphi
\renewcommand\epsilon\varepsilon
\renewcommand\hat\widehat
\renewcommand\tilde\widetilde
\renewcommand\vec\overrightarrow
\renewcommand\bar\overline
\newcommand\fl[1]{\left\lfloor #1\right\rfloor}
\newcommand\llbracket{[\![}
\newcommand\rrbracket{]\!]}
\newcommand\bbr[2]{\llbracket #1,#2\rrbracket}
\newcommand\todo{{\bf TODO }}
\newcommand\prob{\mathbb P}
\newcommand\esp{\mathbb E}
\newcommand\var{\mathbb V}
\newcommand\tribu{\mathfrak T}
\newcommand\stirling[2]{\begin{bmatrix}#1\\#2\end{bmatrix}}$

# Nombres de Stirling de première espèce

Marc Lorenzi

13 mai 2025

In [ ]:
import time

## Introduction

Pour tous $n,k\in\N$, $\mathfrak S_{n,k}$ est l'ensemble des permutations de $\mathfrak S_n$ possédant $k$ orbites. On note 

$$\stirling n k=|\mathfrak S_{n,k}|$$

Les entiers $\stirling n k$ sont les *nombres de Stirling de première espèce*.

La fonction `stirling` renvoie la matrice des $\stirling n k$ pour $n,k\in\bbr0N$.

In [ ]:
def stirling(N):
    cs = [[0 for k in range(N + 1)] for n in range(N + 1)]
    cs[0][0] = 1
    for n in range(1, N + 1):
        for k in range(1, n + 1):
            cs[n][k] = cs[n - 1][k - 1] + (n - 1) * cs[n - 1][k]
    return cs

In [ ]:
N = 10
S = stirling(N)
for n in range(N + 1):
    for k in range(N + 1):
        print('%8d' % S[n][k], end='')
    print()

La complexité temporelle et la complexité spatiale de `stirling` sont en $O(N^2)$. 

Pour de grandes valeurs de $N$, la complexité spatiale peut poser problème. La fonction `stirling2` renvoie la ligne $N$ du tableau ci-dessus avec une complexité spatiale seulement en $O(N)$.

In [ ]:
def stirling2(N):
    cs = (N + 1) * [0]
    cs[0] = 1
    for n in range(1, N + 1):
        cs1 = (N + 1) * [0]
        for k in range(1, n + 1):
            cs1[k] = cs[k - 1] + (n - 1) * cs[k]
        cs = cs1
    return cs

In [ ]:
stirling2(10)

On peut maintenant calculer $\stirling{1000}{500}$ en temps et espace raisonnables.

In [ ]:
stirling2(1000)[500]

## Vérifications

On a l'union disjointe

$$\mathfrak S_n=\bigcup_{k=0}^n\mathfrak S_{n,k}$$

et donc

$$\sum_{k=0}^n\stirling n k=n!$$

In [ ]:
def factorielle(n):
    p = 1
    for k in range(1, n + 1):
        p = p * k
    return p

In [ ]:
print(sum(stirling2(1000)) == factorielle(1000))

## MémoÏsation

En utilisant directement la relation de récurrence sur les nombres de Stirling, on obtient la fonction récursive `stirling3` suivante.

In [ ]:
def stirling3(n, k):
    if n == 0:
        if k == 0: return 1
        else: return 0
    elif k == 0: return 0
    else:
        return stirling3(n - 1, k - 1) + (n - 1) * stirling3(n - 1, k)        

In [ ]:
[stirling3(10, k) for k in range(12)]

Cette fonction renvoie le bon résultat mais sa complexité temporelle est exécrable. Calculons $\stirling{26}{13}$.

In [ ]:
t1 = time.time()
a = stirling3(26, 13)
t2 = time.time()
print(a)
print(stirling2(26)[13])
print(t2 - t1)

Le lecteur pourra évaluer `stirling3(30, 15)`, revenir 3 jours plus tard ... puis redémarrer sa machine plantée😀.

La raison de la mauvaise complexité de cette fonction est qu'elle recalcule indéfiniment les mêmes nombres de Stirling. Pour éviter cela, on peut utiliser une technique de mémoïsation. 

Pour *mémoïser* une fonction $f$, on crée un **cache**. Pour calculer $f(x)$ :

- Cas 1 : $f(x)$ est dans le cache. On renvoie la valeur en zéro seconde.
- Cas 2 : $f(x)$ n'est pas dans le cache. On appelle la fonction $f$, on met le résultat dans le cache, et on est ramenés au premier cas.

Python permet d'automatiser cette technique. Ci-dessous, on crée un dictionnaire `memo` (le cache) dont les clés sont des couples $(n,k)$. On crée ensuite une fonction `memoize` (on peut l'appeler comme on veut) prenant en paramètre une fonction $f$ de 2 variables (ce sera plus tard une fonction `stirling4`). La fonction `memoize` renvoie une fonction `aux` qui fait ce que l'on vient de dire.

In [ ]:
memo = {}
def memoize(f):
    
    def aux(n, k):
        if (n, k) not in memo: 
            memo[(n, k)] = f(n, k)
        return memo[(n, k)]
    
    return aux

Maintenant, faisons un copier-coller de `stirling3` et rajoutons simplement le **décorateur** `@memoize` avant la définition de la fonction.

In [ ]:
@memoize
def stirling4(n, k):
    if n == 0:
        if k == 0: return 1
        else: return 0
    elif k == 0: return 0
    else:
        return stirling4(n - 1, k - 1) + (n - 1) * stirling4(n - 1, k)        

In [ ]:
t1 = time.time()
a = stirling4(26, 13)
t2 = time.time()
print(a)
print(stirling2(26)[13])
print(t2 - t1)

La fonction `stirling4` renvoie le résultat en zéro seconde. Histoire d'être vraiment certains, tentons le calcul de $\stirling{1000}{500}$.

In [ ]:
t1 = time.time()
a = stirling4(1000, 500)
t2 = time.time()
print(a)
#print(stirling2(1000)[500])
print(t2 - t1)

Il faut seulement quelques dixièmes de seconde pour obtenir le résultat. 

Trop beau pour être vrai ! Y aurait-il un piège ? Évidemment. Recalculons le même nombre de Stirling.

In [ ]:
t1 = time.time()
a = stirling4(1000, 500)
t2 = time.time()
print(a)
#print(stirling2(1000)[500])
print(t2 - t1)

Mince, maintenant il faut zéro seconde. Eh bien oui, c'est la mémoïsation. Alors, où est le souci ? Il est dans la mémoire de l'ordinateur ...

In [ ]:
len(memo)

Notre dictionnaire `memo` contient 376251 entrées. Et il va grossir, grossir, grossir ... imaginez un instant un programme qui utiliserait des milliers de fonctions mémoïsées ! Et si quelqu'un me demande quelle est la complexité de `stirling4`, je lui réponds quoi ? Ma réponse serait : « cela dépend de ce que tu as fait les trois derniers jours ».